description.

In [1]:
import os
import math
import numpy as np
import pandas as pd
from ast import literal_eval
import itertools
import arviz as az
import scipy.stats as st
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.patches as  mpatches
pd.options.mode.chained_assignment = None  # default='warn'

from helper_functions import *

agent_center_x = 972
agent_center_y = 288

In [75]:
example_eye = pre_process_eye_data(pd.read_csv(("../../../../Volumes/KMODyS_1/Data Moonlander II/AB31IA/eye_data/AB31IA_eye_tracking_output_1Afake_13.csv"), index_col=False))
example_eye


time_tag     TimeTag    LeftEyeX    LeftEyeY  LeftPupilDiameter  \
0        0.0000  26248.1615 -593.837524 -362.671265          73.800781   
1        0.0005  26248.1620 -593.250488 -362.729248          73.808594   
2        0.0010  26248.1625 -593.054871 -361.844421          73.800781   
3        0.0015  26248.1630 -592.979614 -361.375000          73.828125   
4        0.0020  26248.1635 -593.220398 -362.017761          73.847656   
...         ...         ...         ...         ...                ...   
83844   41.9220  26290.0835  207.159912  333.038574          74.738281   
83845   41.9225  26290.0840  206.505005  332.657593          74.699219   
83846   41.9230  26290.0845  206.302490  333.237305          74.644531   
83847   41.9235  26290.0850  207.159912  333.619385          74.648438   
83848   41.9240  26290.0855  206.481201  333.068237          74.617188   

        RightEyeX   RightEyeY  RightPupilDiameter   DigitalIn  LeftBlink  ...  \
0     -582.697937 -301.979431           69.183594  16777215.0        0.0  ...   
1     -582.599121 -302.243591           69.183594  16777215.0        0.0  ...   
2     -582.246094 -302.270081           69.199219  16777215.0        0.0  ...   
3     -582.006104 -302.309753           69.203125  16777215.0        0.0  ...   
4     -582.359070 -302.653015           69.195312  16777215.0        0.0  ...   
...           ...         ...                 ...         ...        ...  ...   
83844  149.545349  363.879150           70.664062  16777215.0        0.0  ...   
83845  148.939697  363.983154           70.683594  16777215.0        0.0  ...   
83846  148.871948  363.952026           70.683594  16777215.0        0.0  ...   
83847  148.643982  364.592041           70.656250  16777215.0        0.0  ...   
83848  148.466919  364.200928           70.636719  16777215.0        0.0  ...   

       distance_to_spaceship_in_pixel  distance_to_spaceship  \
0                          837.709652              17.173810   
1                          837.576352              17.171238   
2                          837.080386              17.161667   
3                          836.817548              17.156595   
4                          837.374212              17.167337   
...                               ...                    ...   
83844                      192.295371               4.057896   
83845                      191.680755               4.044969   
83846                      191.701999               4.045416   
83847                      192.231567               4.056554   
83848                      191.624391               4.043784   

       distant_fixation  Saccade  saccadeOnset  N_saccade  \
0                     0      0.0             0        NaN   
1                     0      0.0             0        NaN   
2                     0      0.0             0        NaN   
3                     0      0.0             0        NaN   
4                     0      0.0             0        NaN   
...                 ...      ...           ...        ...   
83844                 0      0.0             0        NaN   
83845                 0      0.0             0        NaN   
83846                 0      0.0             0        NaN   
83847                 0      0.0             0        NaN   
83848                 0      0.0             0        NaN   

       saccade_direction_x  saccade_direction_y  saccade_amplitude_in_pixel  \
0                      NaN                  NaN                 1024.727728   
1                      NaN                  NaN                 1024.727728   
2                      NaN                  NaN                 1024.727728   
3                      NaN                  NaN                 1024.727728   
4                      NaN                  NaN                 1024.727728   
...                    ...                  ...                         ...   
83844                  NaN                  NaN                 1024.727728   
83845      

In [76]:
example_input = pre_process_input_data(pd.read_csv(("../../../../Volumes/KMODyS_1/Data Moonlander II/AB31IA/data/AB31IA_output_1Afake_done_13.csv"), index_col=False))
example_input


frame  trial  attempt  time_played      time_tag  level_size_y  \
0         0      1        1     0.000997  26248.162366         14094   
1         1      1        1     0.016920  26248.162366         14094   
2         2      1        1     0.033911  26248.162366         14094   
3         3      1        1     0.050236  26248.162366         14094   
4         4      1        1     0.067229  26248.162366         14094   
...     ...    ...      ...          ...           ...           ...   
2292   2292      1        1    40.237779  26248.162366         14094   
2293   2293      1        1    40.253651  26248.162366         14094   
2294   2294      1        1    40.272593  26248.162366         14094   
2295   2295      1        1    40.288436  26248.162366         14094   
2296   2296      1        1    41.843606  26248.162366         14094   

      player_pos  collision current_input  current_drift  ...  \
0     [954, -86]      False           NaN            0.0  ...   
1     [954, -82]      False           NaN            0.0  ...   
2     [954, -78]      False           NaN            0.0  ...   
3     [954, -74]      False           NaN            0.0  ...   
4     [954, -70]      False           NaN            0.0  ...   
...          ...        ...           ...            ...  ...   
2292  [954, 270]      False           NaN            0.0  ...   
2293  [954, 270]      False           NaN            0.0  ...   
2294  [954, 270]      False           NaN            0.0  ...   
2295  [954, 270]      False           NaN            0.0  ...   
2296  [954, 270]      False           NaN            0.0  ...   

     visible_drift_tiles expectability  SoC adjusted_time_tag start_input  \
0                     []           NaN  NaN      26248.163363         NaN   
1                     []           NaN  NaN      26248.179285         NaN   
2                     []           NaN  NaN      26248.196277         NaN   
3                     []           NaN  NaN      26248.212602         NaN   
4                     []           NaN  NaN      26248.229595         NaN   
...                  ...           ...  ...               ...         ...   
2292                  []           NaN  NaN      26288.400145         NaN   
2293                  []           NaN  NaN      26288.416017         NaN   
2294                  []           NaN  NaN      26288.434958         NaN   
2295                  []           NaN  NaN      26288.450801         NaN   
2296                  []           7.0  NaN      26290.005972         NaN   

      N_input input_change  input_duration  drift_tile_onset  \
0         NaN          NaN             NaN                 0   
1         NaN          NaN             NaN                 0   
2         NaN          NaN             NaN                 0   
3         NaN          NaN             NaN                 0   
4         NaN          NaN             NaN                 0   
...       ...          ...             ...               ...   
2292      NaN          NaN             NaN                 0   
2293      NaN          NaN             NaN                 0   
2294      NaN          NaN             NaN                 0   
2295      NaN          NaN             NaN                 0   
2296      NaN          NaN             NaN                 0   

      drift_effect_onset  
0                      0  
1                      0  
2                      0  
3                      0  
4                      0  
...                  ...  
2292                   0  
2293                   0  
2294                   0  
2295                   0  
2296                   0  

[2297 rows x 26 columns]

In [77]:
example_input.columns

Index(['frame', 'trial', 'attempt', 'time_played', 'time_tag', 'level_size_y',
       'player_pos', 'collision', 'current_input', 'current_drift',
       'drift_variation', 'drift_type', 'level_done', 'visible_obstacles',
       'last_walls_tile', 'adjacent_wall_tiles_x_pos', 'visible_drift_tiles',
       'expectability', 'SoC', 'adjusted_time_tag', 'start_input', 'N_input',
       'input_change', 'input_duration', 'drift_tile_onset',
       'drift_effect_onset'],
      dtype='object')

In [78]:
#root_dir = os.getcwd()

data_dir = "../../../../Volumes/KMODyS_1/Data Moonlander II/"

target_string = "output"
target_string_eye_tracking = "eye_tracking"

runs = []

for subdir, dirs, files in os.walk(data_dir):
    for file in files:
        if target_string_eye_tracking in file:
            runs.append(file)

# all data files have in their names a triplet for identification...       
# triplet coding: level, drift_tiles, drift_type(block)

In [79]:
runs.remove('._AB31IA_eye_tracking_output_1Ainvisible_71.csv')  # don't know what that is
runs

['UB02TZ_eye_tracking_output_2Anormal_46.csv',
 'UB02TZ_eye_tracking_output_2Anormal_45.csv',
 'UB02TZ_eye_tracking_output_4Binvisible_25.csv',
 'UB02TZ_eye_tracking_output_3Bfake_36.csv',
 'UB02TZ_eye_tracking_output_5Bnormal_48.csv',
 'UB02TZ_eye_tracking_output_3Bnormal_47.csv',
 'UB02TZ_eye_tracking_output_6Afake_38.csv',
 'UB02TZ_eye_tracking_output_4Binvisible_20.csv',
 'UB02TZ_eye_tracking_output_4Afake_31.csv',
 'UB02TZ_eye_tracking_output_3Ano_drift_08.csv',
 'UB02TZ_eye_tracking_output_3Binvisible_10.csv',
 'UB02TZ_eye_tracking_output_1Afake_37.csv',
 'UB02TZ_eye_tracking_output_5Bfake_35.csv',
 'UB02TZ_eye_tracking_output_2Binvisible_14.csv',
 'UB02TZ_eye_tracking_output_1Binvisible_22.csv',
 'UB02TZ_eye_tracking_output_6Binvisible_11.csv',
 'UB02TZ_eye_tracking_output_2Binvisible_12.csv',
 'UB02TZ_eye_tracking_output_6Bno_drift_06.csv',
 'UB02TZ_eye_tracking_output_6Bfake_40.csv',
 'UB02TZ_eye_tracking_output_4Anormal_28.csv',
 'UB02TZ_eye_tracking_output_6Binvisible_17.csv

In [80]:
# filter the content for trials in snippets df
eye_data_complete = pd.DataFrame()

# slow but explicit for-loop...
for run in runs:
    
    tmp = run.split('_')
    id_code = tmp[0]
    level = tmp[4][0]
    drift_variation = tmp[4][1]
    block = tmp[4][2:]
    exp_trial = tmp[-1][:2]
    
    tmp_data = pre_process_eye_data(pd.read_csv((f"../../../../Volumes/KMODyS_1/Data Moonlander II/{id_code}/eye_data/{run}"), index_col=False))

    tmp_data["ID"] = id_code
    tmp_data["level"] = level
    tmp_data["drift_variation"] = drift_variation
    tmp_data["block"] = block
    tmp_data["trial"] = exp_trial
    
    tmp_data = tmp_data[tmp_data.fixationOnset == 1]
    
    eye_data_complete = pd.concat([eye_data_complete, tmp_data])

In [81]:
len(eye_data_complete)

137190

In [2]:
# saving progress
#eye_data_complete.to_csv('fixations_moonlander_ii.csv', sep=',')
eye_data_complete = pd.read_csv('fixations_moonlander_ii.csv', index_col=False)
eye_data_complete = eye_data_complete.drop(['Unnamed: 0'], axis=1)
eye_data_complete

time_tag    TimeTag    LeftEyeX    LeftEyeY  LeftPupilDiameter  \
0         0.1065  8165.5590 -156.296082  154.567993          80.121094   
1         0.3370  8165.7895   32.532288  110.495605          72.691406   
2         0.6085  8166.0610  -28.652100  433.660889          64.687500   
3         2.3820  8167.8345  -24.058411  192.690063          71.847656   
4         4.4195  8169.8720  -13.013733  141.884155          76.308594   
...          ...        ...         ...         ...                ...   
137185   38.5275  2162.6615  -41.162720  229.162170          77.734375   
137186   38.5965  2162.7305  -37.416077  232.766541          77.632812   
137187   39.1830  2163.3170  -70.609924  141.657532          78.164062   
137188   40.2205  2164.3545  -24.001343  245.489441          79.976562   
137189   40.5720  2164.7060  -47.975586  207.509827          78.546875   

         RightEyeX   RightEyeY  RightPupilDiameter   DigitalIn  LeftBlink  \
0      -134.207001  147.855225           79.156250  16777215.0        0.0   
1        71.567017  126.318970           70.757812  16777215.0        0.0   
2        -5.017090  408.541382           65.238281  16777215.0        0.0   
3        97.408997  239.887573           68.980469  16777215.0        0.0   
4        97.704285  224.859253           71.671875  16777215.0        0.0   
...            ...         ...                 ...         ...        ...   
137185 -242.333344  171.571381           75.515625  16777215.0        0.0   
137186 -238.578278  185.883636           74.484375  16777215.0        0.0   
137187 -188.085114   49.140228           76.265625  16777215.0        0.0   
137188 -242.265594  165.670258           79.199219  16777215.0        0.0   
137189 -256.155243  150.242523           77.292969  16777215.0        0.0   

        ...  N_saccade  saccade_direction_x  saccade_direction_y  \
0       ...        NaN                  NaN                  NaN   
1       ...        NaN                  NaN                  NaN   
2       ...        NaN                  NaN                  NaN   
3       ...        NaN                  NaN                  NaN   
4       ...        NaN                  NaN                  NaN   
...     ...        ...                  ...                  ...   
137185  ...        NaN                  NaN                  NaN   
137186  ...        NaN                  NaN                  NaN   
137187  ...        NaN                  NaN                  NaN   
137188  ...        NaN                  NaN                  NaN   
137189  ...        NaN                  NaN                  NaN   

        saccade_amplitude_in_pixel  saccade_amplitude      ID  level  \
0                       732.104336                NaN  UB02TZ      2   
1                       732.104336                NaN  UB02TZ      2   
2                       732.104336                NaN  UB02TZ      2   
3                       732.104336                NaN  UB02TZ      2   
4                       732.104336                NaN  UB02TZ      2   
...                            ...                ...     ...    ...   
137185                         NaN                NaN      10      1   
137186                         NaN                NaN      10      1   
137187                         NaN                NaN      10      1   
137188                         NaN                NaN      10      1   
137189                         NaN                NaN      10      1   

        drift_variation   block  trial  
0                     A  normal     46  
1                     A  normal     46  
2                     A  normal     46  
3                     A  normal     46  
4                     A  normal     46  
...                 ...     ...    ...  
137185                B  normal     31  
137186                B  normal     31  
137187                B  normal     31  
137188                B  normal     31  
137189                B  normal     31  

[137190 rows x 46 c

In [3]:
np.unique(eye_data_complete.block)

array(['fake', 'invisible', 'no', 'normal'], dtype=object)

'no' == no_drift. Due to the '_', I split it before unintentionally...; 'normal' are also the blocks that have only normal drift (visible). 'normal' could be the block in between the manipulation blocks.

In [4]:
eye_data_complete['drift_type'] = eye_data_complete.block

In [9]:

#eye_data_complete.loc[eye_data_complete.block == 'no' or eye_data_complete.block == 'normal', ['block']] = 'no_drift'

for index, row in eye_data_complete.iterrows():
    if eye_data_complete.loc[index,'block'] == 'no' or eye_data_complete.loc[index,'block'] == 'normal':
        eye_data_complete.loc[index,'block'] = 'no_drift'


In [10]:
np.unique(eye_data_complete.block)

array(['fake', 'invisible', 'no_drift'], dtype=object)

In [13]:
np.unique(eye_data_complete.ID)

array(['10', 'AB31IA', 'AH29LN', 'AY09IN', 'EM20HI', 'ER29AS', 'ES29UL',
       'HI12OE', 'IE11IA', 'IE21OL', 'KO22AT', 'LB20US', 'NK02EN',
       'OT30OC', 'RE10RS', 'RI17IO', 'RO30OL', 'UB02TZ', 'UE25LI',
       'ZI08RN'], dtype=object)

In [14]:
N_visible_obs_col = []
Dist_to_closest_obstacle_col = []
N_visible_drift_col = []
done_col = []

for index, row in eye_data_complete.iterrows():
    
    #if row.block == 'no' or 'normal':
    #    block = 'no_drift'
    #else:
    #    block = row.block
    
    # only consider runs that were successfully completed
    input_file_name_done = f'{row.ID}_output_{row.level}{str(row.drift_variation)}{row.block}_done_{row.trial}.csv'
    
    #input_file_name_crashed = f'{row.ID}_output_{row.level}{str(row.drift_variation)}{row.block}_crashed_{row.trial}.csv'
    
    path = f'../../../../Volumes/KMODyS_1/Data Moonlander II/{row.ID}/data/'
    
    file_found = False
    
    for subdir, dirs, files in os.walk(path):
        for data_file in files:
            if input_file_name_done == data_file:
                file_found = True
                
                print(f'found: {data_file}')

                input_data = pre_process_input_data(pd.read_csv(f'{path}/{data_file}', index_col=False))

                closest_frame = input_data.iloc[(input_data['time_played'] - row.time_tag).abs().argsort()[0]]

                distances = []
                for obstacle in closest_frame.visible_obstacles:
                    dist_squared = np.power(np.abs(obstacle[0] - agent_center_x), 2) + np.power(np.abs(obstacle[1] - agent_center_y), 2)
                    distances.append(np.sqrt(dist_squared))

                if len(distances) > 0:
                    Dist_to_closest_obstacle = np.min(distances)
                elif len(distances) == 0:
                    Dist_to_closest_obstacle = np.nan

                N_visible_obstacles = len(closest_frame.visible_obstacles)
                N_visible_drifts = len(closest_frame.visible_drift_tiles)

                N_visible_obs_col.append(N_visible_obstacles)
                Dist_to_closest_obstacle_col.append(Dist_to_closest_obstacle)
                N_visible_drift_col.append(N_visible_drifts)
                
                done_col.append(True)
            
            #elif input_file_name_crashed in str(data_file):
            #    file_found = True
            #
            #    #print(f'searching for {data_file}')
            #
            #    input_data = pre_process_input_data(pd.read_csv(f'{path}/{data_file}', index_col=False))
            #
            #    closest_frame = input_data.iloc[(input_data['time_played'] - row.time_tag).abs().argsort()[0]]
            #
            #    distances = []
            #    for obstacle in closest_frame.visible_obstacles:
            #        dist_squared = np.power(np.abs(obstacle[0] - agent_center_x), 2) + np.power(np.abs(obstacle[1] - agent_center_y), 2)
            #        distances.append(np.sqrt(dist_squared))
            #
            #    if len(distances) > 0:
            #        Dist_to_closest_obstacle = np.min(distances)
            #    elif len(distances) == 0:
            #        Dist_to_closest_obstacle = np.nan
            #
            #    N_visible_obstacles = len(closest_frame.visible_obstacles)
            #    N_visible_drifts = len(closest_frame.visible_drift_tiles)
            #
            #    N_visible_obs_col.append(N_visible_obstacles)
            #    Dist_to_closest_obstacle_col.append(Dist_to_closest_obstacle)
            #    N_visible_drift_col.append(N_visible_drifts)
            #    
            #    done_col.append(False)
    
    if not file_found:
        print(f'did not find: {data_file}')
        
        N_visible_obs_col.append(np.nan)
        Dist_to_closest_obstacle_col.append(np.nan)
        N_visible_drift_col.append(np.nan)
        done_col.append(np.nan)
        

found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_

found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_done_46.csv
found: UB02TZ_output_2Ano_drift_

found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB0

found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB0

found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB02TZ_output_4Binvisible_done_25.csv
found: UB0

...

found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done_42.csv
found: 10_output_3Bfake_done

found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output_4Binvisible_done_18.csv
found: 10_output

found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done_39.csv
found: 10_output_1Bfake_done

found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output_6Binvisible_done_28.csv
found: 10_output

found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv
found: 10_output_1Bno_drift_done_31.csv


In [17]:
#### FIX ####
eye_data_complete.insert (41, 'N_visible_obstacles', N_visible_obs_col)
eye_data_complete.insert (41, 'Dist_to_closest_obstacles_in_pixel', Dist_to_closest_obstacle_col)
eye_data_complete.insert (41, 'N_visible_drift_tiles', N_visible_drift_col)
eye_data_complete.insert (41, 'done', done_col)

eye_data_complete['Dist_to_closest_obstacles'] = eye_data_complete.apply(lambda row: pixel_to_degree(row.Dist_to_closest_obstacles_in_pixel), axis=1)

In [15]:
np.unique(eye_data_complete['block'])

array(['fake', 'invisible', 'no_drift'], dtype=object)

In [16]:
np.unique(eye_data_complete['drift_type'])

array(['fake', 'invisible', 'no', 'normal'], dtype=object)

In [18]:
eye_data_complete.groupby(['block'])['N_visible_obstacles'].mean()

block
fake         4.096243
invisible    4.099435
no_drift     4.201195
Name: N_visible_obstacles, dtype: float64

In [20]:
eye_data_complete[eye_data_complete.drift_type != 'normal'].groupby(['block'])['N_visible_obstacles'].mean()

block
fake         4.096243
invisible    4.099435
no_drift     4.069003
Name: N_visible_obstacles, dtype: float64

In [21]:
eye_data_complete.groupby(['block'])['fixation_duration'].mean()

block
fake         0.194626
invisible    0.198517
no_drift     0.189947
Name: fixation_duration, dtype: float64

In [22]:
eye_data_complete[eye_data_complete.drift_type != 'normal'].groupby(['block'])['fixation_duration'].mean()

block
fake         0.194626
invisible    0.198517
no_drift     0.162667
Name: fixation_duration, dtype: float64

In [19]:
# drop unnecessary columns for fixation data
eye_data_complete = eye_data_complete.drop(labels=["saccade_amplitude", "saccade_amplitude_in_pixel", "saccade_direction_y", "saccade_direction_x", "saccadeOnset", "N_saccade", "Saccade"], axis = 1)

eye_data_complete.to_csv('fixations_moonlander_ii.csv', sep=',')


# Building SoC data

In [44]:
data_dir = "../../../../Volumes/KMODyS_1/Data Moonlander II/"

output_string = "output"

eye_string = "eye_tracking"
training_string = "training"


runs = []

for subdir, dirs, files in os.walk(data_dir):
    for file in files:
        # potentially only going for crashed or done data
        if eye_string not in file and training_string not in file and output_string in file:
            runs.append(file)

In [46]:
runs.remove('._UB02TZ_output_1Ainvisible_done_21.csv') # don't know what that is
runs

['UB02TZ_output_6Bfake_done_40.csv',
 'UB02TZ_output_1Afake_done_37.csv',
 'UB02TZ_output_4Binvisible_done_25.csv',
 'UB02TZ_output_1Ainvisible_done_21.csv',
 'UB02TZ_output_6Afake_done_38.csv',
 'UB02TZ_output_1Bfake_crashed_42.csv',
 'UB02TZ_output_1Ano_drift_done_09.csv',
 'UB02TZ_output_2Bno_drift_done_03.csv',
 'UB02TZ_output_5Afake_done_34.csv',
 'UB02TZ_output_1Bno_drift_done_30.csv',
 'UB02TZ_output_6Ainvisible_done_16.csv',
 'UB02TZ_output_3Bfake_done_36.csv',
 'UB02TZ_output_3Binvisible_crashed_10.csv',
 'UB02TZ_output_6Bno_drift_done_06.csv',
 'UB02TZ_output_2Bfake_done_33.csv',
 'UB02TZ_output_5Ainvisible_crashed_26.csv',
 'UB02TZ_output_2Binvisible_crashed_12.csv',
 'UB02TZ_output_4Afake_done_31.csv',
 'UB02TZ_output_5Ainvisible_crashed_18.csv',
 'UB02TZ_output_6Binvisible_crashed_11.csv',
 'UB02TZ_output_12ANone_done_02.csv',
 'UB02TZ_output_6Ano_drift_done_29.csv',
 'UB02TZ_output_4Binvisible_crashed_20.csv',
 'UB02TZ_output_5Ainvisible_done_27.csv',
 'UB02TZ_output_2Ain

In [55]:
#%%capture --no-stderr

soc_data = pd.DataFrame()


for run in runs:
    
    tmp = run.split('_')
    id_code = tmp[0]
    level = tmp[2][0]
    drift_variation = tmp[2][1]
    block = tmp[2][2:]
    if block == 'no' or block == 'normal':
        block = 'no_drift'
    exp_trial = tmp[-1][:2]
    
    # don't need last trials
    if int(level) > 6:
        continue
    
    path = data_dir + str(id_code) + "/data/"
    
    tmp_input_data = pre_process_input_data(pd.read_csv((f"{path}/{run}"), index_col=False))
    
    time_played = tmp_input_data["time_played"].iloc[-1]
    N_attempt = tmp_input_data["attempt"].iloc[-1]
    done = tmp_input_data['level_done'].iloc[-1]
    soc_rating = tmp_input_data['SoC'].iloc[-1]
    
    # writing to a temporal data frame
    tmp_data = pd.DataFrame({'ID': id_code,
                             'level': level,
                             'block': block,
                             'N_fixations': [np.nan],
                             'N_distant_fixations': [np.nan],
                             'trial': exp_trial,
                             'time_played': time_played,
                             'N_attempt': N_attempt,
                             'done': done,
                             'SoC': soc_rating})
    
    # eye_data
    path = data_dir + str(id_code) + "/eye_data/"
    if block == 'no_drift':
        try:
            tmp_eye_data = pre_process_eye_data(pd.read_csv(f"{path}/{id_code}_eye_tracking_output_{level}{drift_variation}{block}_{exp_trial}.csv"))
        except:
            tmp_eye_data = pre_process_eye_data(pd.read_csv(f"{path}/{id_code}_eye_tracking_output_{level}{drift_variation}normal_{exp_trial}.csv"))

    tmp_data["N_fixations"].iloc[0] = np.max(tmp_eye_data.N_fixation)
    tmp_data["N_distant_fixations"].iloc[0] = np.sum(tmp_eye_data.distant_fixation)                                                    
    
    soc_data = pd.concat([soc_data, tmp_data])

#soc_data
